In [19]:
#!/usr/bin/env python
# coding: utf-8

# In[1]:


import numpy as np
from   scipy.optimize import minimize
import pandas as pd
import matplotlib.pyplot as plt


# #### Theory

# ![image.png](attachment:image.png)

# #### Preliminary Calculation

# In[2]:

In [20]:
PmmHg = 440.8 
TC    = 9.158144271
zis    = [0.66,0.135,0.162,0.043]

In [21]:
def AntoinePsat(coeff,TC):
    A,B,C = coeff
    return 10**(A-B/(TC + C))

In [22]:
coeffs = [[7.94917,1657.462,227.02],
          [7.5788,863.35,273.15],
          [6.49454,255.6784,266.55],
          [6.69147,319.0117,266.7]]


In [23]:
""" Calculate Psats """
Psats = [AntoinePsat(coeff,TC) for coeff in coeffs]
Psats  

[8.537355065914953, 33160.18044351948, 369137.6636043228, 342796.30727095477]

In [24]:
""" Calculate Kis"""
Kis = np.divide(Psats,PmmHg)
Kis


array([1.93678654e-02, 7.52272696e+01, 8.37426642e+02, 7.77668574e+02])

In [25]:
# define the mass balance
def vapor_phase_mass_balance(V,zis):
    """
    Equation 10.17 SVA
    """
    return np.abs(1-sum([(zi*Ki)/(1+V*(Ki-1)) for zi,Ki in list(zip(zis,Kis))]))

# minimize vapor_phase_mass_balance to solve for V

F_vapor_phase_mass_balance = lambda x : vapor_phase_mass_balance(x,zis)
res = minimize(F_vapor_phase_mass_balance, x0 = 0.5 ,method='Nelder-Mead', tol=1e-6)


# evaluate L and V
if res.success:
    V,L  = res.x[0],1-res.x[0]
else:
    print('Did not converge')
    raise


In [26]:
""" evaluate yis"""
yis = [(zi*Ki)/(1+V*(Ki-1)) for zi,Ki in list(zip(zis,Kis))]
yis

[0.019254965906916017,
 0.38406230477729975,
 0.4715420278978388,
 0.12514042283686558]

In [27]:
""" evaluate xis"""
xis = [yi/Ki for yi,Ki in list(zip(yis,Kis))]
xis

[0.9941707831334012,
 0.0051053601543027535,
 0.0005630845789828888,
 0.00016091742301905547]

In [28]:
L*xis[0],1*zis[0]*0.99

(0.65339999728938, 0.6534)

In [29]:
zis    = [0.66,0.135,0.162,0.043]

In [30]:
def calcT98(TC,zis):
    """ Calculate Psats """
    Psats = [AntoinePsat(coeff,TC) for coeff in coeffs]

    """ Calculate Kis"""
    Kis = np.divide(Psats,PmmHg)
    
    """ solve for the vapor fraction,V"""
    F_vapor_phase_mass_balance = lambda x : vapor_phase_mass_balance(x,zis)
    res = minimize(F_vapor_phase_mass_balance, x0 = 0.5 ,method='Nelder-Mead', tol=1e-6)
    
    # evaluate L and V
    if res.success:
        V,L  = res.x[0],1-res.x[0]
    else:
        print('Did not converge')
        raise
        
    """ evaluate yis"""
    yis = [(zi*Ki)/(1+V*(Ki-1)) for zi,Ki in list(zip(zis,Kis))]
    
    """ evaluate xis"""
    xis = [yi/Ki for yi,Ki in list(zip(yis,Kis))]
        
    return [np.abs(L*xis[0] - (1*zis[0]*0.98)),yis[0]]
                            

F_calcT98 = lambda x : calcT98(x,zis)[0]

In [31]:
T98 = minimize(F_calcT98, x0 = 10 ,method='Nelder-Mead', tol=1e-6)

In [32]:
T98 = T98.x[0]
T98

19.905107498168945

In [33]:
# #### Effect of Composition to T98

# In[15]:


"""water_to_carbondioxide_mass_ratios""" 
r1s = np.linspace(0.05,2,11)
"""wetcarbondioxide_to_air_mole_ratios"""
r2s = 1-np.linspace(0.00,0.40,11) 

In [34]:
r1 = r1s[0]
r2 = r2s[0]

In [35]:
results = []

for r1 in r1s:
    for r2 in r2s:

        mCO2   = 1
        mwater = r1*mCO2

        nCO2   = mCO2/ 44.01
        nwater = mwater / 18.01528

        z1_pure = nwater / (nwater + nCO2)
        z2_pure = nCO2   / (nwater + nCO2)

        zs  = [    r2*z1_pure,
                   r2*z2_pure,
                   0.79*(1 - r2*z1_pure - r2*z2_pure),
                   0.21*(1 - r2*z1_pure - r2*z2_pure)]

        zijs = [np.round(z,3) for z in zs]


        """define a lambda funtion at the calculated zijs"""
        F_calcT98 = lambda x : calcT98(x,zijs)[0]
        """solve for T98"""
        T98 = minimize(F_calcT98, x0 = 50 ,method='Nelder-Mead', tol=1e-6) 

        """append the result and the calculation parameter levels"""
        results.append({'zH2O' : zijs[0],
                        'zCO2' : zijs[1],
                        'zN2'  : zijs[2],
                        'zO2'  : zijs[3],
                        'r1'   : r1,
                        'r2'   : 1-r2,
                        'yH2O' : calcT98(T98.x[0],zijs)[1],
                        'T98'  : T98.x[0]})

In [36]:
results = pd.DataFrame(results)
results.head()

zH2O   zCO2    zN2    zO2    r1    r2      yH2O        T98
0  0.109  0.891 -0.000 -0.000  0.05  0.00  0.002403 -19.445789
1  0.104  0.856  0.032  0.008  0.05  0.04  0.002280 -20.161733
2  0.100  0.820  0.063  0.017  0.05  0.08  0.002182 -20.759943
3  0.096  0.784  0.095  0.025  0.05  0.12  0.002085 -21.381680
4  0.091  0.749  0.126  0.034  0.05  0.16  0.001966 -22.193559

In [37]:
df=results.pivot('r1','r2','yH2O')
df

r2         0.00      0.04      0.08      0.12      0.16      0.20      0.24  \
r1                                                                            
0.050  0.002403  0.002280  0.002182  0.002085  0.001966  0.001871  0.001777   
0.245  0.011811  0.011061  0.010348  0.009669  0.009062  0.008441  0.007846   
0.440  0.021381  0.019616  0.018075  0.016586  0.015214  0.013945  0.012821   
0.635  0.031056  0.028006  0.025211  0.022829  0.020694  0.018694  0.016955   
0.830  0.040917  0.036093  0.032009  0.028500  0.025555  0.022866  0.020486   
1.025  0.050890  0.043965  0.038326  0.033781  0.029791  0.026477  0.023494   
1.220  0.060927  0.051696  0.044438  0.038565  0.033705  0.029612  0.026114   
1.415  0.071202  0.059247  0.050184  0.043050  0.037275  0.032358  0.028355   
1.610  0.081214  0.066234  0.055573  0.047118  0.040417  0.034965  0.030437   
1.805  0.091741  0.073664  0.060515  0.050717  0.043308  0.037178  0.032291   
2.000  0.102358  0.080387  0.065397  0.054160  0.045827  0.039220  0.033845   

r2         0.28      0.32      0.36      0.40  
r1                                             
0.050  0.001661  0.001568  0.001477  0.001364  
0.245  0.007277  0.006731  0.006208  0.005706  
0.440  0.011722  0.010696  0.009780  0.008878  
0.635  0.015371  0.013863  0.012535  0.011310  
0.830  0.018363  0.016458  0.014797  0.013230  
1.025  0.020964  0.018644  0.016579  0.014788  
1.220  0.023089  0.020444  0.018112  0.016040  
1.415  0.024934  0.021974  0.019388  0.017109  
1.610  0.026614  0.023341  0.020505  0.018025  
1.805  0.028075  0.024500  0.021514  0.018836  
2.000  0.029383  0.025513  0.022305  0.019526

In [38]:
plt.figure(dpi=100)
X=df.columns.values
Y=df.index.values
Z=df.values
x,y=np.meshgrid(X, Y)
plt.contourf(x, y, Z) #the NAN will be plotted as white spaces
plt.colorbar(label = 'y$_{water}$')
plt.xlabel('mole air / (mole CO$_2$ + H$_2$O)')
plt.ylabel('mass H$_2$O / mass CO$_2$')

NameError: name 'plt' is not defined

In [ ]:
df=results.pivot('r1','r2','T98')
df

In [ ]:
plt.figure(dpi=100)
X=df.columns.values
Y=df.index.values
Z=df.values
x,y=np.meshgrid(X, Y)
plt.contourf(x, y, Z) #the NAN will be plotted as white spaces
plt.colorbar(label = 'T$_{98}$,[°C]')
plt.xlabel('mole air / (mole CO$_2$ + H$_2$O)')
plt.ylabel('mass H$_2$O / mass CO$_2$')
plt.show()